In [1]:
import sys
import warnings
warnings.filterwarnings("ignore")
import os
import pickle
from sklearn.metrics import accuracy_score, precision_score, recall_score, f1_score, cohen_kappa_score
import numpy as np
import matplotlib
from matplotlib import pylab
import seaborn as sns
from IPython.display import display
from tabulate import tabulate
from collections import Counter, defaultdict
import re
import copy
from scipy import stats
from scipy.stats import wilcoxon, entropy
import pandas as pd
from utils import *
sns.set_style("dark")
sns.set(font_scale=1.00)

FILENAMES = ['OBESIDAD', 'OBESIDAD_TIPOS', 'FUMADOR'] 

MODELS = [
        'nb-n1', 'nb-fregex', 
        'xgb-n1', 'xgb-fregex',
        'svm-n1', 'svm-fregex', 
        'rf-n1', 'rf-fregex', 
        'bert', 
        'setfit', 
         ]

FOLDS = 2
BATCH = 64

LABELS_CLASSES = {
    'OBESIDAD': ['NEGATIVE', 'POSITIVE'],
    'OBESIDAD_TIPOS': ['MODERATE', 'SEVERE', 'MORBID'],
    'FUMADOR': ['NEGATIVE', 'POSITIVE'],
    }

METRIC = 'F1'

pylab.rcParams["legend.facecolor"] = "white"
pylab.rcParams['figure.facecolor'] = "white"
H = 10
W = 15
CURVES = dict( [ (MODEL, ['_PL_', '_AL_']) for MODEL in MODELS] )

COLORS = {
          'nb-n1_PL_': 'b',
          'nb-n2_PL_': 'b',
          'nb-fregex_PL_': 'b',
          'nb-n1_AL_': 'b',
          'nb-n2_AL_': 'b',
          'nb-fregex_AL_': 'b',
          'xgb-n1_PL_': 'k',
          'xgb-n2_PL_': 'k',
          'xgb-fregex_PL_': 'k',
          'xgb-n1_AL_': 'k',
          'xgb-n2_AL_': 'k',
          'xgb-fregex_AL_': 'k',
          'rf-n1_PL_': 'r',
          'rf-n2_PL_': 'r',
          'rf-fregex_PL_': 'r',
          'rf-n1_AL_': 'r',
          'rf-n2_AL_': 'r',
          'rf-fregex_AL_': 'r',
          'svm-n1_PL_': 'g',
          'svm-n2_PL_': 'g',
          'svm-fregex_PL_': 'g',
          'svm-n1_AL_': 'g',
          'svm-n2_AL_': 'g',
          'svm-fregex_AL_': 'g',
          'bert_PL_': 'c',
          'bert_AL_': 'c',
          'setfit_PL_': 'm',
          'setfit_AL_': 'm',
}
LINES = {
          'nb-n1_PL_': '-',
          'nb-n2_PL_': '-',
          'nb-fregex_PL_': '-',   
          'nb-n1_AL_': '--',
          'nb-n2_AL_': '--',
          'nb-fregex_AL_': 'dotted',    
          'xgb-n1_PL_': '-',
          'xgb-n2_PL_': '-',
          'xgb-fregex_PL_': '-',
          'xgb-n1_AL_': '--',
          'xgb-n2_AL_': '--',
          'xgb-fregex_AL_': 'dotted',
          'rf-n1_PL_': '-',
          'rf-n2_PL_': '-',
          'rf-fregex_PL_': '-',
          'rf-n1_AL_': '--',
          'rf-n2_AL_': '--',
          'rf-fregex_AL_': 'dotted',
          'svm-n1_PL_': '-',
          'svm-n2_PL_': '-',
          'svm-fregex_PL_': '-',
          'svm-n1_AL_': '--',
          'svm-n2_AL_': '--',
          'svm-fregex_AL_': 'dotted',
          'bert_PL_': '-',
          'bert_AL_': '--',
          'setfit_PL_': '-',
          'setfit_AL_': '--',
}

LABELS = {
          'nb-n1_PL_': 'NB&N1 (PL)',
          'nb-n2_PL_': 'NB&N2 (PL)',
          'nb-fregex_PL_': 'NB&RegExes (PL)',
          'nb-n1_AL_': 'NB&N1 (AL)',
          'nb-n2_AL_': 'NB&N2 (AL)',
          'nb-fregex_AL_': 'NB&RegExes (AL)',
          'xgb-n1_PL_': 'XGB&N1 (PL)',
          'xgb-n2_PL_': 'XGB&N2 (PL)',
          'xgb-fregex_PL_': 'XGB&RegExes (PL)',
          'xgb-n1_AL_': 'XGB&N1 (AL)',
          'xgb-n2_AL_': 'XGB&N2 (AL)',
          'xgb-fregex_AL_': 'XGB&RegExes (AL)',
          'rf-n1_PL_': 'RF&N1 (PL)',
          'rf-n2_PL_': 'RF&N2 (PL)',
          'rf-fregex_PL_': 'XGB&RegExes (PL)',
          'rf-n1_AL_': 'RF&N1 (AL)',
          'rf-n2_AL_': 'RF&N2 (AL)',
          'rf-fregex_AL_': 'RF&RegExes (AL)',
          'svm-n1_PL_': 'SVM&N1 (PL)',
          'svm-n2_PL_': 'SVM&N2 (PL)',
          'svm-fregex_PL_': 'SVM&RegExes (PL)',
          'svm-n1_AL_': 'SVM&N1 (AL)',
          'svm-n2_AL_': 'SVM&N2 (AL)',
          'svm-fregex_AL_': 'SVM&RegExes (AL)',
          'bert_PL_': 'BERT (PL)',
          'bert_AL_': 'BERT (AL)',
          'setfit_PL_': 'SetFit (PL)',
          'setfit_AL_': 'SetFit (AL)',
}
TITLES = {
          'OBESIDAD': 'OBESITY STATUS DS',
          'OBESIDAD_TIPOS': 'OBESITY TYPES DS',
          'FUMADOR': 'SMOKING STATUS DS',
}

LW = 4
MS = 5
S = 150

None of PyTorch, TensorFlow >= 2.0, or Flax have been found. Models won't be available and only tokenizers, configuration and file/data utilities can be used.


In [2]:
print('FOLDS:', FOLDS, '\n')

idx = 0
values = np.arange(0.8, 1, 0.01)
x_y_curves = {'0_'+METRIC.upper()+'(%)>=': values}
results_aulc = defaultdict(list)
results_base = defaultdict(list)
results_curves = defaultdict(list)
results_features = defaultdict(list)
results_hyps = defaultdict(list)

for FILENAME in FILENAMES:
    #print('-'*30)
    #print(FILENAME)
    idx+=1
    
    for MODEL in MODELS:
        #print(MODEL)

        for CURVE in CURVES[MODEL]:
            #print(CURVE)
            if 'PL' in CURVE and 'regex' in MODEL or 'PL' in CURVE and MODEL in ['bert', 'setfit']:
                continue
            
            CURVE_AUX = CURVE.replace('_', '')
            y = []  #learning curves
            
            for k in range(FOLDS):
                with open( os.path.join( os.getcwd(), 'out', 'RESULTSLC', CURVE_AUX, FILENAME, FILENAME+'_'+MODEL+'_'+CURVE_AUX+'_k'+str(k+1)+'.pkl' ), 'rb') as a:
                    results_lc = pickle.load(a)
                    y_b = []
                    s_b = []

                    s_aux = copy.deepcopy(results_lc[0])  #entropy values
                    x_aux = copy.deepcopy(results_lc[1])  #x-samples values
                    y_aux = copy.deepcopy(results_lc[2])  #pred on test
                    yl_aux = copy.deepcopy(results_lc[3]) #pred on unlabeled
                    yc_aux = copy.deepcopy(results_lc[4]) #labels on unlabeled
                    d_aux = copy.deepcopy(results_lc[5])  #distribution on test (clf vs rex)
                    h_aux = copy.deepcopy(results_lc[6])  #hyperparameters
                    f_aux = copy.deepcopy(results_lc[7])  #number of features
                    yt_aux = copy.deepcopy(results_lc[8]) #labels on test
                    
                    results_hyps[MODEL+'_'+FILENAME].append(h_aux)
                    results_features[MODEL+CURVE+FILENAME].append(f_aux)
                                                
                    for ypredb in y_aux:
                        if METRIC == 'F1':
                            if len(LABELS_CLASSES[FILENAME])>2:
                                pre =  precision_score(yt_aux, ypredb.argmax(axis=1), average='weighted') 
                                rec = recall_score(yt_aux, ypredb.argmax(axis=1), average='weighted') 
                            else:
                                pre =  precision_score(yt_aux, ypredb.argmax(axis=1), pos_label=1) 
                                rec = recall_score(yt_aux, ypredb.argmax(axis=1), pos_label=1) 
                            f1 = (2*pre*rec)/(pre+rec)
                            y_b.append( f1 )
                            
                            if 'AL' in CURVE:
                                acc = accuracy_score(yt_aux, ypredb.argmax(axis=1))
                                results_base[MODEL+'_PRE_'+FILENAME] = np.round(pre,2)
                                results_base[MODEL+'_REC_'+FILENAME] = np.round(rec,2)
                                results_base[MODEL+'_F1_'+FILENAME]  = np.round(f1,2)
                                results_base[MODEL+'_ACC_'+FILENAME]  = np.round(acc, 2)
                            
                        elif METRIC == 'ACC':
                            acc = accuracy_score(yt_aux, ypredb.argmax(axis=1))
                            y_b.append( acc )
                                  
                    y.append(y_b)
                                        
            y = np.array(y)
            ye = np.std(y, axis=0) 
            y = np.mean(y, axis=0)
            
            results_curves[MODEL+'_'+FILENAME+CURVE] = copy.deepcopy(y)
            results_aulc[MODEL+'_'+FILENAME+CURVE] = np.round(AULC(x_aux, y),2) 

            fig1 = pylab.figure(1, figsize=(H, W), dpi=800)
            fig1.subplots_adjust(hspace=0.25)
            #fig1 = pylab.figure(1, figsize=(H*1.7,int(W)/4.0),dpi=800)
            pylab.subplot(len(FILENAMES), 1, idx)
            #pylab.subplot(1, len(FILENAMES), idx)
            pylab.title(TITLES[FILENAME], fontweight='bold')
            '''
            pylab.xscale('log')  
            xmin, xmax = min(x_aux), max(x_aux) 
            log_min = np.log10(xmin)
            log_max = np.log10(xmax)
            xticks_pos = [
                10**log_min,                   
                10**log_max                    
            ]
            xticks_labels = [
                fr'$10^{log_min:.0f}$',         
                fr'$10^{log_max:.0f}$'         
            ]
            pylab.xticks(xticks_pos, xticks_labels)
            '''
            pylab.plot(x_aux, y, COLORS[MODEL+CURVE], linestyle=LINES[MODEL+CURVE], label=LABELS[MODEL+CURVE], lw=LW, ms=MS)
            #print('Curve', y)
            pylab.fill_between(x_aux, y-ye, y+ye, facecolor=COLORS[MODEL+CURVE],  alpha=0.05)
            pylab.ylim([0.40, 1.00])
            pylab.grid(True)
            pylab.xlabel('Number of training examples'.upper() )
            pylab.ylabel( ('Average '+METRIC).upper() )
            if idx==2:
                pylab.legend(loc='upper center', bbox_to_anchor=(0.5, -1.40), shadow=False, ncol=5)
                #pylab.legend( loc='upper center', bbox_to_anchor=(0.50, -0.2), shadow=False, ncol=5 )

            x_y = []
            for val in values:
                xy = '-'
                for i in range(len(x_aux)):
                    if y[i]>=val and xy=='-':
                        xy = x_aux[i]
                        break
                x_y.append(xy)
            x_y_curves[FILENAME+'-'+MODEL+'-'+CURVE.replace('_', '')] = x_y

pylab.show()

fig1.savefig( os.path.join(os.getcwd(), 'out', 'Figures', 'lc.pdf'), bbox_inches='tight', format="pdf" )

FOLDS: 2 



In [3]:
print('RESULTS')
for FILENAME in FILENAMES:
    for MODEL in MODELS:
        print(FILENAME, MODEL, 'PRE', results_base[MODEL+'_PRE_'+FILENAME])
        print(FILENAME, MODEL, 'REC', results_base[MODEL+'_REC_'+FILENAME]) 
        print(FILENAME, MODEL, 'F1', results_base[MODEL+'_F1_'+FILENAME] )
        print(FILENAME, MODEL, 'ACC', results_base[MODEL+'_ACC_'+FILENAME] )

RESULTS
OBESIDAD nb-n1 PRE 0.92
OBESIDAD nb-n1 REC 0.94
OBESIDAD nb-n1 F1 0.93
OBESIDAD nb-n1 ACC 0.9
OBESIDAD nb-fregex PRE 0.98
OBESIDAD nb-fregex REC 0.93
OBESIDAD nb-fregex F1 0.95
OBESIDAD nb-fregex ACC 0.93
OBESIDAD xgb-n1 PRE 0.99
OBESIDAD xgb-n1 REC 0.97
OBESIDAD xgb-n1 F1 0.98
OBESIDAD xgb-n1 ACC 0.97
OBESIDAD xgb-fregex PRE 0.99
OBESIDAD xgb-fregex REC 0.97
OBESIDAD xgb-fregex F1 0.98
OBESIDAD xgb-fregex ACC 0.97
OBESIDAD svm-n1 PRE 0.98
OBESIDAD svm-n1 REC 0.96
OBESIDAD svm-n1 F1 0.97
OBESIDAD svm-n1 ACC 0.95
OBESIDAD svm-fregex PRE 0.97
OBESIDAD svm-fregex REC 0.96
OBESIDAD svm-fregex F1 0.97
OBESIDAD svm-fregex ACC 0.95
OBESIDAD rf-n1 PRE 0.98
OBESIDAD rf-n1 REC 0.95
OBESIDAD rf-n1 F1 0.97
OBESIDAD rf-n1 ACC 0.95
OBESIDAD rf-fregex PRE 1.0
OBESIDAD rf-fregex REC 0.97
OBESIDAD rf-fregex F1 0.98
OBESIDAD rf-fregex ACC 0.97
OBESIDAD bert PRE 0.98
OBESIDAD bert REC 0.96
OBESIDAD bert F1 0.97
OBESIDAD bert ACC 0.96
OBESIDAD setfit PRE 0.99
OBESIDAD setfit REC 0.97
OBESIDAD setf

In [4]:
print('AULC')
for key in results_aulc:
    if '_AL_' in key:
        print(key, results_aulc[key])

AULC
nb-n1_OBESIDAD_AL_ 0.92
nb-fregex_OBESIDAD_AL_ 0.95
xgb-n1_OBESIDAD_AL_ 0.95
xgb-fregex_OBESIDAD_AL_ 0.96
svm-n1_OBESIDAD_AL_ 0.96
svm-fregex_OBESIDAD_AL_ 0.97
rf-n1_OBESIDAD_AL_ 0.97
rf-fregex_OBESIDAD_AL_ 0.98
bert_OBESIDAD_AL_ 0.96
setfit_OBESIDAD_AL_ 0.98
nb-n1_OBESIDAD_TIPOS_AL_ 0.69
nb-fregex_OBESIDAD_TIPOS_AL_ 0.81
xgb-n1_OBESIDAD_TIPOS_AL_ 0.8
xgb-fregex_OBESIDAD_TIPOS_AL_ 0.9
svm-n1_OBESIDAD_TIPOS_AL_ 0.77
svm-fregex_OBESIDAD_TIPOS_AL_ 0.84
rf-n1_OBESIDAD_TIPOS_AL_ 0.8
rf-fregex_OBESIDAD_TIPOS_AL_ 0.89
bert_OBESIDAD_TIPOS_AL_ 0.74
setfit_OBESIDAD_TIPOS_AL_ 0.87
nb-n1_FUMADOR_AL_ 0.77
nb-fregex_FUMADOR_AL_ 0.84
xgb-n1_FUMADOR_AL_ 0.85
xgb-fregex_FUMADOR_AL_ 0.88
svm-n1_FUMADOR_AL_ 0.85
svm-fregex_FUMADOR_AL_ 0.86
rf-n1_FUMADOR_AL_ 0.85
rf-fregex_FUMADOR_AL_ 0.9
bert_FUMADOR_AL_ 0.81
setfit_FUMADOR_AL_ 0.88


In [5]:
print('LC')
for FILENAME in FILENAMES:
    dct = {'0_F1(%)>=':x_y_curves['0_F1(%)>=']}
    for key in x_y_curves:
        if FILENAME+'-' in key:
            dct[key] = x_y_curves[key]
    df = pd.DataFrame.from_dict(dct)
    table_df = tabulate(df, headers = 'keys', tablefmt = 'psql', showindex=False).replace('|', '&')
    table_df = re.sub(r'^\&', ' ', table_df, flags=re.M)
    table_df = re.sub(r'\&$', r'\\\\ ', table_df, flags=re.M)
    print( table_df )
    del dct

LC
+-------------+---------------------+---------------------+-------------------------+----------------------+----------------------+--------------------------+----------------------+----------------------+--------------------------+---------------------+---------------------+-------------------------+--------------------+----------------------+
    0_F1(%)>= & OBESIDAD-nb-n1-PL   & OBESIDAD-nb-n1-AL   & OBESIDAD-nb-fregex-AL   & OBESIDAD-xgb-n1-PL   & OBESIDAD-xgb-n1-AL   & OBESIDAD-xgb-fregex-AL   & OBESIDAD-svm-n1-PL   & OBESIDAD-svm-n1-AL   & OBESIDAD-svm-fregex-AL   & OBESIDAD-rf-n1-PL   & OBESIDAD-rf-n1-AL   & OBESIDAD-rf-fregex-AL   & OBESIDAD-bert-AL   & OBESIDAD-setfit-AL   \\ 
 -------------+---------------------+---------------------+-------------------------+----------------------+----------------------+--------------------------+----------------------+----------------------+--------------------------+---------------------+---------------------+-------------------------+--

In [6]:
CURVES = dict( [ (MODEL, ['_AL_']) for MODEL in MODELS] )

print('FOLDS:', FOLDS, '\n')

idx = 0

for FILENAME in FILENAMES:
    #print('-'*30)
    #print(FILENAME)
    idx+=1
    
    for MODEL in MODELS:
        #print(MODEL)

        for CURVE in CURVES[MODEL]:            
            CURVE_AUX = CURVE.replace('_', '')
            y = []  #learning curves
            s = []  #scores-AL
            
            dst_al = defaultdict(list)
            for k in range(FOLDS):
                with open( os.path.join( os.getcwd(), 'out', 'RESULTSLC', CURVE_AUX, FILENAME, FILENAME+'_'+MODEL+'_'+CURVE_AUX+'_k'+str(k+1)+'.pkl' ), 'rb') as a:
                    results_lc = pickle.load(a)
                    s_b = []

                    s_aux = copy.deepcopy(results_lc[0])  #entropy values
                    x_aux = copy.deepcopy(results_lc[1])  #x-samples values
                    y_aux = copy.deepcopy(results_lc[2])  #pred on test
                    yl_aux = copy.deepcopy(results_lc[3]) #pred on unlabeled
                    yc_aux = copy.deepcopy(results_lc[4]) #labels on unlabeled
                    d_aux = copy.deepcopy(results_lc[5])  #distribution on test (clf vs rex)
                    h_aux = copy.deepcopy(results_lc[6])  #hyperparameters
                    f_aux = copy.deepcopy(results_lc[7])  #number of features
                    yt_aux = copy.deepcopy(results_lc[8]) #labels on test
                                       
                    for spredb in s_aux:
                        s_b.append( np.var(spredb[:BATCH]) )
                    s.append(s_b)
                    NPOINTS = len(y_b)
                    
            y = results_curves[MODEL+'_'+FILENAME+CURVE]
            s = np.array(s)
            se = np.std(s, axis=0)
            s = np.mean(s, axis=0)
             
            fig2 = pylab.figure(2, figsize=(H, W),dpi=800)
            fig2.subplots_adjust(hspace=0.25)
            #fig2 = pylab.figure(2, figsize=(int(H*1.00),int(W*1.28)), dpi=800)
            pylab.subplot(len(FILENAMES), 1, idx)
            #pylab.subplot(1, len(FILENAMES), idx)
            pylab.title(TITLES[FILENAME], fontweight='bold')

            '''
            pylab.xscale('log')  
            xmin, xmax = min(x_aux[1:]), max(x_aux) 
            log_min = np.log10(xmin)
            log_max = np.log10(xmax)
            xticks_pos = [
                10**log_min,                   
                10**log_max                    
            ]
            xticks_labels = [
                fr'$10^{log_min:.0f}$',         
                fr'$10^{log_max:.0f}$'         
            ]
            pylab.xticks(xticks_pos, xticks_labels)
            pylab.plot(x_aux[1:], s, COLORS[MODEL+CURVE], label=LABELS[MODEL+CURVE], linestyle=LINES[MODEL+CURVE], 
                       lw=LW, 
                       ms=MS)
            pylab.fill_between(x_aux[1:], s-se, s+se, facecolor=COLORS[MODEL+CURVE],  alpha=0.05)
            '''
            
            pylab.plot(x_aux[:-1]+1, s, COLORS[MODEL+CURVE], label=LABELS[MODEL+CURVE], linestyle=LINES[MODEL+CURVE], 
                       lw=LW, 
                       ms=MS)
            pylab.fill_between(x_aux[:-1]+1, s-se, s+se, facecolor=COLORS[MODEL+CURVE],  alpha=0.05)
            
            m = SC(s) 
            pylab.ylim([-0.01, 0.40])
            pylab.grid(True)
            pylab.xlabel( 'iteration number'.upper() )
            pylab.ylabel( 'Average variance'.upper() )
            #pylab.xticks(x_aux[:-1]+1, np.arange(1, len(x_aux[:-1])+1))
            if idx==2:
                #pylab.legend( loc='upper center', bbox_to_anchor=(0.50, -1.40), shadow=False, ncol=5 )
                pylab.legend( loc='upper center', bbox_to_anchor=(0.50, -1.40), shadow=False, ncol=5 )
            if m<len(s)-1-2:
                print('SC', FILENAME, MODEL, CURVE, 
                      'Deltay', y[m]-y[m+2], 
                      'x_%', (100*x_aux[m+2])/x_aux[-1],
                     )

            else:
                diff = len(y)-m-1
                print('SC', FILENAME, MODEL, CURVE, 'Deltay', y[m]-y[m+diff], 'x_%', (100*x_aux[m+diff])/x_aux[-1])


pylab.show()

fig2.savefig( os.path.join(os.getcwd(), 'out', 'Figures', 'var.pdf'), bbox_inches='tight', format="pdf" )


FOLDS: 2 

SC OBESIDAD nb-n1 _AL_ Deltay -0.010680386610907644 x_% 51.68236877523553
SC OBESIDAD nb-fregex _AL_ Deltay 0.003616475223929494 x_% 43.06864064602961
SC OBESIDAD xgb-n1 _AL_ Deltay -0.2663406430464035 x_% 43.06864064602961
SC OBESIDAD xgb-fregex _AL_ Deltay 0.04686475155236525 x_% 51.68236877523553
SC OBESIDAD svm-n1 _AL_ Deltay 0.0014397836812810594 x_% 51.68236877523553
SC OBESIDAD svm-fregex _AL_ Deltay -0.0014165154239944577 x_% 43.06864064602961
SC OBESIDAD rf-n1 _AL_ Deltay -0.004382376734155091 x_% 60.296096904441455
SC OBESIDAD rf-fregex _AL_ Deltay -0.01474483000587834 x_% 60.296096904441455
SC OBESIDAD bert _AL_ Deltay 0.005723445758564205 x_% 51.68236877523553
SC OBESIDAD setfit _AL_ Deltay 0.0073702639041172135 x_% 100.0
SC OBESIDAD_TIPOS nb-n1 _AL_ Deltay -0.014133100148402411 x_% 77.10843373493977
SC OBESIDAD_TIPOS nb-fregex _AL_ Deltay 0.004729014754275007 x_% 66.09294320137694
SC OBESIDAD_TIPOS xgb-n1 _AL_ Deltay -0.12407405368270152 x_% 66.09294320137694
SC

In [7]:
print('HYPERPARAMETERS')
aux = defaultdict(list)
for MODEL in MODELS:
    for FILENAME in FILENAMES:
        keys = results_hyps[MODEL+'_'+FILENAME][0] 
        for key in keys:
            for k in range(FOLDS):
                aux[MODEL+'_'+key].append( results_hyps[MODEL+'_'+FILENAME][k][key] )
    
for key in aux:
    print(key, Counter(aux[key]))

HYPERPARAMETERS
nb-n1_alpha Counter({1: 4, 0.75: 1, 0.25: 1})
nb-fregex_alpha Counter({0: 3, 0.25: 2, 1: 1})
xgb-n1_random_state Counter({42: 6})
xgb-n1_gamma Counter({1: 2, 0.5: 2, 10: 2})
xgb-n1_learning_rate Counter({0.1: 4, 1.0: 1, 0.3: 1})
xgb-n1_n_estimators Counter({10: 4, 50: 2})
xgb-fregex_random_state Counter({42: 6})
xgb-fregex_gamma Counter({0: 3, 1: 2, 0.5: 1})
xgb-fregex_learning_rate Counter({0.1: 3, 0.3: 2, 0.8: 1})
xgb-fregex_n_estimators Counter({10: 4, 50: 1, 200: 1})
svm-n1_random_state Counter({42: 6})
svm-n1_probability Counter({True: 6})
svm-n1_C Counter({1: 6})
svm-n1_kernel Counter({'linear': 6})
svm-fregex_random_state Counter({42: 6})
svm-fregex_probability Counter({True: 6})
svm-fregex_C Counter({1: 5, 10: 1})
svm-fregex_kernel Counter({'linear': 5, 'rbf': 1})
rf-n1_random_state Counter({42: 6})
rf-n1_criterion Counter({'gini': 5, 'entropy': 1})
rf-n1_n_estimators Counter({500: 4, 100: 1, 1000: 1})
rf-fregex_random_state Counter({42: 6})
rf-fregex_criterion 

In [8]:
print('FEATURES')
for MODEL in MODELS:
    for FILENAME in FILENAMES:
        aux = []
        aux.extend( list(np.array( results_features[MODEL+CURVE+FILENAME] )[:,-1] ) )     
        print(FILENAME, MODEL, np.round(np.mean(aux),0))

FEATURES
OBESIDAD nb-n1 3520.0
OBESIDAD_TIPOS nb-n1 3517.0
FUMADOR nb-n1 3041.0
OBESIDAD nb-fregex 2330.0
OBESIDAD_TIPOS nb-fregex 2626.0
FUMADOR nb-fregex 2683.0
OBESIDAD xgb-n1 3520.0
OBESIDAD_TIPOS xgb-n1 3517.0
FUMADOR xgb-n1 3041.0
OBESIDAD xgb-fregex 2330.0
OBESIDAD_TIPOS xgb-fregex 2626.0
FUMADOR xgb-fregex 2683.0
OBESIDAD svm-n1 3520.0
OBESIDAD_TIPOS svm-n1 3517.0
FUMADOR svm-n1 3041.0
OBESIDAD svm-fregex 2330.0
OBESIDAD_TIPOS svm-fregex 2626.0
FUMADOR svm-fregex 2683.0
OBESIDAD rf-n1 3520.0
OBESIDAD_TIPOS rf-n1 3517.0
FUMADOR rf-n1 3041.0
OBESIDAD rf-fregex 2330.0
OBESIDAD_TIPOS rf-fregex 2626.0
FUMADOR rf-fregex 2683.0
OBESIDAD bert 768.0
OBESIDAD_TIPOS bert 768.0
FUMADOR bert 768.0
OBESIDAD setfit 768.0
OBESIDAD_TIPOS setfit 768.0
FUMADOR setfit 768.0
